In [ ]:
# pip install torch_xla -q

In [ ]:
# ! nvidia-smi -L

In [1]:
!pip install gradio diffusers gTTS together -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.8/41.8 kB 2.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.2/57.2 MB 30.3 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 320.4/320.4 kB 18.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 82.3 MB/s eta 0:00:00:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.6/70.6 kB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 94.8/94.8 kB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.5/73.5 kB 4.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 4.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 450.5/450.5 kB 25.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 131.3/131.3 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.2/11.2 MB 106.1 MB/s eta 0:00:0000:010:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.2/73.2 kB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
# import torch_xla.core.xla_model as xm
# tpu = xm.xla_device()

In [2]:
import torch
from diffusers import TextToVideoSDPipeline, DiffusionPipeline
from diffusers.utils import export_to_video
import gradio as gr
from transformers import AutoTokenizer, AutoModelForCausalLM
import PIL
from io import BytesIO
from gtts import gTTS
import time
from pydub import AudioSegment
import nltk
from together import Together
import base64


The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

In [3]:
# tokenizer = AutoTokenizer.from_pretrained("MBZUAI/LaMini-GPT-774M")
# model0 = AutoModelForCausalLM.from_pretrained("MBZUAI/LaMini-GPT-774M")

tokenizer = AutoTokenizer.from_pretrained("ParisNeo/LLama-3.2-3B-Lollms-Finetuned-GGUF")
model0 = AutoModelForCausalLM.from_pretrained("ParisNeo/LLama-3.2-3B-Lollms-Finetuned-GGUF", ignore_mismatched_sizes=True)

# tokenizer = AutoTokenizer.from_pretrained("gokaygokay/tiny_llama_chat_description_to_prompt", cache_dir = '/kaggle/working')
# model0 = AutoModelForCausalLM.from_pretrained("gokaygokay/tiny_llama_chat_description_to_prompt", ignore_mismatched_sizes=True, cache_dir = '/kaggle/working')
# model0 = AutoModelForCausalLM.from_pretrained("MJ199999/gpt3_model",ignore_mismatched_sizes=True, from_tf=True)


tokenizer_config.json:   0%|          | 0.00/55.4k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/454 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/996 [00:00<?, ?B/s]

pytorch_model.bin.index.json:   0%|          | 0.00/20.9k [00:00<?, ?B/s]

pytorch_model-00001-of-00002.bin:   0%|          | 0.00/4.97G [00:00<?, ?B/s]

pytorch_model-00002-of-00002.bin:   0%|          | 0.00/1.46G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/234 [00:00<?, ?B/s]

In [4]:
device = torch.device("cuda:1" if torch.cuda.is_available() else "cpu")
model0 = model0.to(device)

In [5]:
from transformers import AutoModelForCausalLM, AutoTokenizer

# Initialize Chat History
def chat_with_llama(user_input, chat_history):
    # Prepare formatted prompt
    prompt = "You are a helpful, respectful and honest general-purpose assistant."
    for user_content, assist_content in chat_history:
        prompt += f"user: {user_content}\n"
        prompt += f"assistant: {assist_content}\n"
    prompt += f"user: {user_input}\n'assistant:"

    # Tokenize and generate response
    inputs = tokenizer(prompt, return_tensors="pt").to("cuda:1")
    output = model0.generate(inputs["input_ids"], max_length=4096, max_new_tokens = 1024, temperature=0.7, max_time = 10.0, repetition_penalty = 1.0)
    response = tokenizer.decode(output[0], skip_special_tokens=True)

    # Extract and append assistant's response
    assistant_reply = response.split("assistant:")[-1].split('user:')[0].strip()
    chat_history.append((user_input, assistant_reply))

    return assistant_reply, chat_history


In [ ]:
# chat_history = []
# answer0, chat_history = chat_with_llama('Hi. My name is Smith', [])
# print(answer0)
# answer1, chat_history = chat_with_llama('What is my name?', chat_history)
# print(answer1)
# answer2, chat_history = chat_with_llama('Can you guess my wife\'s name?', chat_history)
# print(answer2)
# print(chat_history)

In [6]:
api_key='ac2619935e6a25d4bae2890260822fa0379ec7d8726114ff9744a38127bf8525'
client = Together(api_key=api_key)

In [7]:
def chat_api(user_input, chat_history):
    messages = []
    for user_content, assist_content in chat_history:
        messages += [
            {"role":"user", "content":user_content},
            {"role":"assistant", "content":assist_content}
        ]
    messages += [{"role":"user", "content":user_input}]
    
    response = client.chat.completions.create(
        model="meta-llama/Llama-3.3-70B-Instruct-Turbo",
        messages=messages,
    )
    reply = response.choices[0].message.content
    chat_history.append((user_input, reply))
    return reply, chat_history

In [ ]:
# chat_history = []
# answer0, chat_history = chat_api('Hi. My name is Smith', [])
# print(answer0, '\n-----------------------------------------\n')
# answer1, chat_history = chat_api('What is my name?', chat_history)
# print(answer1, '\n-----------------------------------------\n')
# answer2, chat_history = chat_api('Can you guess my wife\'s name?', chat_history)

# # Chat Example
# print(answer2, '\n-----------------------------------------\n')
# print(chat_history)

In [8]:
def tti_api(prompt, num_steps = 25, width = 512, heights = 512):
    response = client.images.generate(
        prompt=prompt,
        model="black-forest-labs/FLUX.1-dev",
        width=width,
        height=heights,
        steps=num_steps,
        n=1,
        response_format="b64_json"
    )
    
    image_data = base64.b64decode(response.data[0].b64_json)
    return image_data

In [9]:
prompt = 'A nice black lexus 570 car running on the snowy road.'
image = tti_api(prompt, num_steps = 25)
image = PIL.Image.open(BytesIO(image))
image.save('result.png')
image.show()

In [10]:
def ttv(prompt, num_steps = 50):
    # Load the text-to-video model from Hugging Face
    model_id = "damo-vilab/text-to-video-ms-1.7b"  # ModelScope Text-to-Video model
    #model_id = "guoyww/animatediff-motion-adapter-v1-5-2"  # ModelScope Text-to-Video 
    
    pipe = TextToVideoSDPipeline.from_pretrained(model_id, torch_dtype=torch.float16, variant="fp16")
    pipe.to("cuda:0")  # Use GPU if available
   
    # Generate video frames
    print("Generating video... This may take some time.")
    with torch.no_grad():
        video_frames = pipe(prompt, num_frames=32, height=256, width=256, num_inference_steps=num_steps).frames[0]
    # Save the generated video
    video_path = export_to_video(video_frames, output_video_path="output_video.mp4")
    return video_path
test_video = ttv('An awesome lexus 570 car running on the snowy road, high quality', num_steps = 50)

model_index.json:   0%|          | 0.00/384 [00:00<?, ?B/s]

Fetching 12 files:   0%|          | 0/12 [00:00<?, ?it/s]

text_encoder/config.json:   0%|          | 0.00/644 [00:00<?, ?B/s]

scheduler/scheduler_config.json:   0%|          | 0.00/465 [00:00<?, ?B/s]

unet/config.json:   0%|          | 0.00/787 [00:00<?, ?B/s]

...

Loading pipeline components...:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


Generating video... This may take some time.


  0%|          | 0/50 [00:00<?, ?it/s]

/usr/lib/python3.10/subprocess.py:1796: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = _posixsubprocess.fork_exec(


In [11]:
# Ensure the sentence tokenizer is downloaded (if not already)
nltk.download('punkt')

# Function to convert text to speech and generate SRT content
def tts(text):
    # Initialize the Google TTS engine with language (e.g., 'en' for English)
    tts = gTTS(text=text, lang='en', slow=False)
    
    # Save to an audio file
    audio_path = "output.mp3"
    tts.save(audio_path)
    
    # Load the audio file with pydub to get the duration
    audio = AudioSegment.from_mp3(audio_path)
    duration_ms = len(audio)  # Duration in milliseconds
    
    # Split the text into sentences using NLTK
    sentences = nltk.sent_tokenize(text)
    
    # Estimate the duration per sentence
    chunk_duration_ms = duration_ms // len(sentences)  # Estimated duration per sentence
    
    # Generate SRT content
    srt_content = ""
    start_time = 0  # Start time of the first subtitle
    for idx, sentence in enumerate(sentences):
        end_time = start_time + chunk_duration_ms
        start_time_formatted = time.strftime('%H:%M:%S', time.gmtime(start_time / 1000)) + ',' + f'{start_time % 1000:03d}'
        end_time_formatted = time.strftime('%H:%M:%S', time.gmtime(end_time / 1000)) + ',' + f'{end_time % 1000:03d}'
        
        srt_content += f"{idx + 1}\n"
        srt_content += f"{start_time_formatted} --> {end_time_formatted}\n"
        srt_content += f"{sentence}\n\n"
        
        start_time = end_time  # Update start time for the next sentence
    
    return audio_path, srt_content

[nltk_data] Downloading package punkt to /usr/share/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [12]:
def tti(prompt, num_steps = 50, width = 512, heights = 512):
    # Load the pre-trained Stable Diffusion pipeline from Hugging Face
    pipe = DiffusionPipeline.from_pretrained("stabilityai/stable-diffusion-2-1")
    #pipe.load_lora_weights("FradigmaDangerYT/dalle-e-mini")
    
    # Move the pipeline to GPU (you can select the GPU with cuda:1 for the second GPU)
    device0 = torch.device("cuda:0")  # Use "cuda:0" for the first GPU, "cuda:1" for the second GPU
    pipe.to(device0)
    print(heights)
    # Generate an image
    image = pipe(prompt, num_inference_steps = num_steps, width = width, height = heights).images[0]  # Generate image from the prompt
    return image


In [13]:
prompt = 'A nice black lexus 570 car running on the snowy road.'
image = tti(prompt, num_steps = 25, width = 320, heights = 240)
# image = PIL.Image.open(BytesIO(image))
image.save('result.png')
image.show()

model_index.json:   0%|          | 0.00/537 [00:00<?, ?B/s]

Fetching 13 files:   0%|          | 0/13 [00:00<?, ?it/s]

text_encoder/config.json:   0%|          | 0.00/633 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.36G [00:00<?, ?B/s]

tokenizer/merges.txt:   0%|          | 0.00/525k [00:00<?, ?B/s]

...

diffusion_pytorch_model.safetensors:   0%|          | 0.00/335M [00:00<?, ?B/s]

vae/config.json:   0%|          | 0.00/611 [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/6 [00:00<?, ?it/s]

240


  0%|          | 0/25 [00:00<?, ?it/s]

In [14]:

# If demo is on, turn off demo
try:
    demo.close()
except:
    pass

with gr.Blocks() as demo:
    gr.Markdown("""
    # Gradio based Text-to-Any Project
    """)
    with gr.Tab(label="Llama-Chat"):
        radios0 = gr.Radio(['use api', 'use loaded model'], value="use api", show_label = False)
        gptDialog = gr.Chatbot(label = "Llama-Chat", max_height=512, min_height=512,
                                       autoscroll= True)
        with gr.Row(equal_height=True):
            prompt0 = gr.Textbox(label = 'Prompt Input', lines = 1, scale = 9, max_lines=2,
                                autofocus=True, autoscroll=True, placeholder='Type your message here...')
            with gr.Column(scale = 1):
                generate_btn0 = gr.Button('generate')
                clear_btn0 = gr.Button('clear')
            
    with gr.Tab(label="Text-to-Image/Video"):
        with gr.Row():
            radios1 = gr.Radio(['use api', 'use loaded model'], value="use api", show_label = False)
            steps = gr.Slider(value = 50, minimum = 20, maximum = 100, step = 1, label = 'num_steps')
            width = gr.Slider(value = 1024, minimum = 240, maximum = 1792, step = 16, label = 'width')
            heights = gr.Slider(value = 512, minimum = 160, maximum = 1792, step = 16, label = 'heights')
            
        with gr.Row():
            outputImg = gr.Image(type='pil',height= 512, width=512, label="Output Image", interactive=False)
            outputVideo = gr.Video(width=512, height=512, label = "Output Video", interactive=False)
        with gr.Row(equal_height=True):
            prompt1 = gr.Textbox(label = 'Prompt Input', lines = 1, scale = 9, max_lines=2,
                                autofocus=True, autoscroll=True, placeholder='Type your message here...')
            with gr.Column(scale = 1):
                generate_btn1 = gr.Button('generate image')
                generate_btn11 = gr.Button('generate video')

    with gr.Tab(label = "Text-to-Speech"):
        outputAudio = gr.Audio(label="Audio Output", interactive = False)
        outputSrt = gr.Textbox(label = 'Script Output', lines = 10, max_lines = 5, placeholder = 'Script output here')
        with gr.Row(equal_height=False):
            prompt2 = gr.Textbox(label = 'Prompt Input', lines = 5, scale = 9, max_lines=5,
                                autofocus=True, autoscroll=True, placeholder='Type your message here...')
            with gr.Column(scale = 1):
                generate_btn2 = gr.Button('generate')
                clear_btn2 = gr.Button('clear')

    with gr.Tab(label = 'About'):
        pass

    def generate_txt(prompt, check, history):
        if check == 'use api':
            response, history = chat_api(prompt, history)
            if response == None:
                gr.Warning('Can not reach api.')
        else:
            response, history = chat_with_llama(prompt, history)
            if response == None:
                gr.Warning('Failed to load model.')
        return '', history
    
    def clear_chat():
        history = []
        gr.Info('Cleaned successfully!')
        return history

    def generate_img(prompt, check, num_steps, width, heights):
        if check == 'use api':
            image = tti_api(prompt, num_steps = num_steps, width = width, heights = heights)
            image = PIL.Image.open(BytesIO(image))
            if not image:
                gr.Warning('Can not reach api')
            gr.Info('Generated Image Successfully!')
        else:
            image = tti(prompt, num_steps = num_steps, width = width, heights = heights)
            gr.Info('Generated Image Successfully!')
        return image
        
    def generate_video(prompt, num_steps):
        video = ttv(prompt, num_steps)
        gr.Info('Generated Video Successfully!')
        return video
        
    def generate_speech(prompt):
        audio, script = tts(prompt)
        gr.Info('Generated Speech Successfully!')                           
        return audio, script
        
    def clear_speech():
        gr.Info('Cleaned Successfully!')
        return None, ''
    
    prompt0.submit(generate_txt, [prompt0, radios0, gptDialog], [prompt0, gptDialog])
    prompt1.submit(generate_img, [prompt1, radios1], [outputImg])

    # generate button click event
    generate_btn0.click(generate_txt, [prompt0, radios0, gptDialog], [prompt0, gptDialog])
    generate_btn1.click(generate_img, [prompt1, radios1, steps, width, heights], [outputImg])
    generate_btn11.click(generate_video, [prompt1, steps], [outputVideo])
    generate_btn2.click(generate_speech, [prompt2], [outputAudio, outputSrt])
    
    # clear button click event
    clear_btn0.click(clear_chat, [], [gptDialog])
    clear_btn2.click(clear_speech, [], [outputAudio, outputSrt])
demo.launch()
        

/usr/local/lib/python3.10/dist-packages/gradio/components/chatbot.py:242: UserWarning: You have not specified a value for the `type` parameter. Defaulting to the 'tuples' format for chatbot messages, but this is deprecated and will be removed in a future version of Gradio. Please set type='messages' instead, which uses openai-style dictionaries with 'role' and 'content' keys.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/gradio/utils.py:1003: UserWarning: Expected 5 arguments for function <function generate_img at 0x799439ab0dc0>, received 2.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/gradio/utils.py:1007: UserWarning: Expected at least 5 arguments for function <function generate_img at 0x799439ab0dc0>, received 2.
  warnings.warn(


* Running on local URL:  http://127.0.0.1:7860
Kaggle notebooks require sharing enabled. Setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

* Running on public URL: https://d2c6c018093abcee72.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
demo.close()